In [19]:
import importlib
import strategies.ema_crossover_v1.strategy as ema_crossover_v1

importlib.reload(ema_crossover_v1)
EMACrossoverRSIStrategy = ema_crossover_v1.EMACrossoverRSIStrategy

## Constants

In [4]:
from datetime import datetime, timezone
from investing_algorithm_framework import BacktestDateRange

evaluation_date_range = BacktestDateRange(
    start_date=datetime(2023, 1, 1, tzinfo=timezone.utc),
    end_date=datetime(2024, 12, 31, tzinfo=timezone.utc),
)

risk_free_rate = 0.027 # (2.7%) Example risk-free rate, adjust
# as needed or let the framework handle it dynamically based on market data.
evaluation_assets = ["BTC/EUR"]
market = "BITVAVO"

## Hyperparameters

Here you can define the hyperparameters for the strategy. Hyperparameters are used to configure the strategy's behavior, such as the lookback period for indicators, thresholds for buy/sell signals, etc. You use hyperparameters to fine-tune the strategy's performance, by grid searching or using other optimization techniques.

In [3]:
from itertools import product

params = {
    "ema_short_period": [50, 75],
    "ema_long_period": [100, 200],
    "rsi_period": [14],
    "rsi_overbought_threshold": [70],
    "rsi_oversold_threshold": [30],
    "alignment_window_size": [12, 24],
    "ema_time_frame": ["1h", "4h", "1d"],
    "rsi_time_frame": ["1h", "4h", "1d"],
}

param_variants = [
    dict(zip(params.keys(), values)) for values in product(*params.values())
]

## Run vector backtest to evaluate the strategy

In [4]:
from tqdm import tqdm
from investing_algorithm_framework import create_app, DataSource

app = create_app()
backtests = []
print(f"Running backtests for {len(param_variants)} parameter combinations...")

for param_variant in tqdm(param_variants):
    strategy = EMACrossoverRSIStrategy(
        time_unit="hour",
        interval=2,
        symbols=["BTC/EUR"],
        data_sources=[
            DataSource(
                symbol="BTC/EUR",
                time_frame=param_variant["ema_time_frame"],
                data_type="OHLCV",
                market=market,
                pandas=True
            ),
            DataSource(
                symbol="BTC/EUR",
                time_frame=param_variant["rsi_time_frame"],
                data_type="OHLCV",
                market=market,
                pandas=True
            )
        ],
        market=market,
        ema_short_period=param_variant["ema_short_period"],
        ema_long_period=param_variant["ema_long_period"],
        rsi_period=param_variant["rsi_period"],
        rsi_oversold_threshold=param_variant["rsi_oversold_threshold"],
        rsi_overbought_threshold=param_variant["rsi_overbought_threshold"],
        alignment_window_size=param_variant["alignment_window_size"],
        ema_time_frame=param_variant["ema_time_frame"],
        rsi_time_frame=param_variant["rsi_time_frame"],
    )
    backtest = app.run_vector_backtest(
        strategy=strategy,
        backtest_date_range=evaluation_date_range,
        initial_amount=10000,
        metadata={
            "params": param_variant,
        },
        risk_free_rate=risk_free_rate
    )
    backtests.append(backtest)


Running backtests for 72 parameter combinations...


  0%|          | 0/72 [00:00<?, ?it/s]

Preparing backtest data:   0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/72 [00:04<?, ?it/s]


KeyError: 'ema_data'

## Rank the vector backtests

In [5]:
from IPython.display import display
from investing_algorithm_framework import get_equity_curve_with_drawdown_chart, rank_results, \
get_rolling_sharpe_ratio_chart, defaults_ranking_weights, \
get_monthly_returns_heatmap_chart

weights = defaults_ranking_weights.copy()
weights["win_rate"] = 2.0  # Give more weight to strategies with higher win rates

ranked_backtests = rank_results(backtests, weights=weights)
for i, backtest in enumerate(ranked_backtests[:5]):
    print(f"Backtest {i + 1}:")
    print(f"  meta_data: {backtest.metadata}")
    print(f"  Name: {backtest.backtest_results.name}")
    print(f"  Final value: {backtest.backtest_metrics.final_value:.2f}")
    print(f"  Total Return: {backtest.backtest_metrics.total_return:.2f} ({backtest.backtest_metrics.total_return_percentage:.2%})")
    print(f"  Sharpe Ratio: {backtest.backtest_metrics.sharpe_ratio:.2f}")
    print(f"  Sortino Ratio: {backtest.backtest_metrics.sortino_ratio:.2f}")
    print(f"  Max Drawdown: {backtest.backtest_metrics.max_drawdown:.2%}")
    print(f"  Win Rate: {backtest.backtest_metrics.win_rate}%")
    print(f"  Profit Factor: {backtest.backtest_metrics.profit_factor:.2f}")
    data = backtest.to_dict()
    equity_drawdown_chart = get_equity_curve_with_drawdown_chart(
        backtest.backtest_metrics.equity_curve,
        backtest.backtest_metrics.drawdown_series
    )
    display(equity_drawdown_chart)
    rolling_sharpe_ratio_fig = get_rolling_sharpe_ratio_chart(
        backtest.backtest_metrics.rolling_sharpe_ratio
    )
    display(rolling_sharpe_ratio_fig)
    monthly_returns_heatmap = get_monthly_returns_heatmap_chart(
        backtest.backtest_metrics.monthly_returns
    )
    display(monthly_returns_heatmap)

Backtest 1:
  meta_data: {'params': {'ema_short_period': 75, 'ema_long_period': 100, 'rsi_period': 14, 'rsi_overbought_threshold': 70, 'rsi_oversold_threshold': 30, 'alignment_window_size': 12, 'ema_time_frame': '1d', 'rsi_time_frame': '4h'}}
  Name: vector_backtest
  Final value: 32035.44
  Total Return: 22035.44 (220.35%)
  Sharpe Ratio: 1.58
  Sortino Ratio: 2.02
  Max Drawdown: 30.17%
  Win Rate: 50.0%
  Profit Factor: 33.45


Backtest 2:
  meta_data: {'params': {'ema_short_period': 75, 'ema_long_period': 100, 'rsi_period': 14, 'rsi_overbought_threshold': 70, 'rsi_oversold_threshold': 30, 'alignment_window_size': 24, 'ema_time_frame': '1d', 'rsi_time_frame': '4h'}}
  Name: vector_backtest
  Final value: 26636.85
  Total Return: 16636.85 (166.37%)
  Sharpe Ratio: 1.35
  Sortino Ratio: 1.74
  Max Drawdown: 30.17%
  Win Rate: 50.0%
  Profit Factor: 6.63


Backtest 3:
  meta_data: {'params': {'ema_short_period': 50, 'ema_long_period': 100, 'rsi_period': 14, 'rsi_overbought_threshold': 70, 'rsi_oversold_threshold': 30, 'alignment_window_size': 24, 'ema_time_frame': '1d', 'rsi_time_frame': '4h'}}
  Name: vector_backtest
  Final value: 22711.38
  Total Return: 12711.38 (127.11%)
  Sharpe Ratio: 1.16
  Sortino Ratio: 1.43
  Max Drawdown: 36.23%
  Win Rate: 50.0%
  Profit Factor: 3.72


Backtest 4:
  meta_data: {'params': {'ema_short_period': 50, 'ema_long_period': 100, 'rsi_period': 14, 'rsi_overbought_threshold': 70, 'rsi_oversold_threshold': 30, 'alignment_window_size': 12, 'ema_time_frame': '4h', 'rsi_time_frame': '1h'}}
  Name: vector_backtest
  Final value: 22392.80
  Total Return: 12392.80 (123.93%)
  Sharpe Ratio: 1.04
  Sortino Ratio: 1.42
  Max Drawdown: 41.56%
  Win Rate: 36.84210526315789%
  Profit Factor: 5.23


Backtest 5:
  meta_data: {'params': {'ema_short_period': 75, 'ema_long_period': 100, 'rsi_period': 14, 'rsi_overbought_threshold': 70, 'rsi_oversold_threshold': 30, 'alignment_window_size': 24, 'ema_time_frame': '1d', 'rsi_time_frame': '1h'}}
  Name: vector_backtest
  Final value: 21175.06
  Total Return: 11175.06 (111.75%)
  Sharpe Ratio: 1.07
  Sortino Ratio: 1.34
  Max Drawdown: 39.81%
  Win Rate: 50.0%
  Profit Factor: 4.10


In [10]:
import pandas as pd
import plotly.graph_objects as go

def line_chart(
    data: pd.DataFrame,
    column: str,
):
    """
    Create a line chart for the specified column in the DataFrame.
    """
    return go.Scatter(
        x=data.index,
        y=data[column],
        mode='lines',
        name=column,
        line=dict(color='blue')
    )

def entry_chart(
    data: pd.DataFrame,
    entry_column: str,
):
    """
    Create a scatter chart for entry points in the DataFrame.
    """
    entry_points = data[data[entry_column] == True]
    return go.Scatter(
        x=entry_points.index,
        y=entry_points["Close"],
        mode="markers",
        name="Entry",
        marker=dict(symbol="triangle-up", color="green", size=10)
    )

def exit_chart(
    data: pd.DataFrame,
    exit_column: str,
):
    """
    Create a scatter chart for exit points in the DataFrame.
    """
    exit_points = data[data[exit_column] == True]
    return go.Scatter(
        x=exit_points.index,
        y=exit_points["Close"],
        mode="markers",
        name="Exit",
        marker=dict(symbol="triangle-down", color="red", size=10)
    )


def crossover_crossunder_chart(
    data,
):
    """
    """
    crossover = data[data["crossover"] == True]
    crossunder = data[data["crossunder"] == True]

    scatter_crossover = go.Scatter(
        x=crossover.index,
        y=crossover["Close"],
        mode="markers",
        name="Crossover",
        marker=dict(symbol="triangle-up", color="green", size=10)
    )

    scatter_crossunder = go.Scatter(
        x=crossunder.index,
        y=crossunder["Close"],
        mode="markers",
        name="Crossunder",
        marker=dict(symbol="triangle-down", color="red", size=10)
    )
    return scatter_crossover, scatter_crossunder

In [21]:
from investing_algorithm_framework import DataSource, download
from pyindicators import ema, crossover, crossunder

param_variant = {
    'ema_short_period': 75,
    'ema_long_period': 100,
    'rsi_period': 14,
    'rsi_overbought_threshold': 70,
    'rsi_oversold_threshold': 30,
    'alignment_window_size':48,
    'ema_time_frame': '1d',
    'rsi_time_frame': '4h'
}
strategy = EMACrossoverRSIStrategy(
    time_unit="hour",
    interval=2,
    symbols=["BTC/EUR"],
    data_sources=[
        DataSource(
            identifier="ema_data",
            symbol="BTC/EUR",
            time_frame=param_variant["ema_time_frame"],
            data_type="OHLCV",
            market=market,
            pandas=True
        ),
        DataSource(
            identifier="rsi_data",
            symbol="BTC/EUR",
            time_frame=param_variant["rsi_time_frame"],
            data_type="OHLCV",
            market=market,
            pandas=True
        )
    ],
    market=market,
    ema_short_period=param_variant["ema_short_period"],
    ema_long_period=param_variant["ema_long_period"],
    rsi_period=param_variant["rsi_period"],
    rsi_oversold_threshold=param_variant["rsi_oversold_threshold"],
    rsi_overbought_threshold=param_variant["rsi_overbought_threshold"],
    alignment_window_size=param_variant["alignment_window_size"],
    ema_time_frame=param_variant["ema_time_frame"],
    rsi_time_frame=param_variant["rsi_time_frame"],
)
ema_data = download(
    symbol="BTC/EUR",
    time_frame=param_variant["ema_time_frame"],
    data_type="OHLCV",
    market=market,
    pandas=True,
    start_date=evaluation_date_range.start_date,
    end_date=evaluation_date_range.end_date
)
test_sample = ema_data.copy()
rsi_data = download(
    symbol="BTC/EUR",
    time_frame=param_variant["rsi_time_frame"],
    data_type="OHLCV",
    market=market,
    pandas=True,
    start_date=evaluation_date_range.start_date,
    end_date=evaluation_date_range.end_date
)
price_data = download(
    symbol="BTC/EUR",
    time_frame="1d",
    data_type="OHLCV",
    market=market,
    pandas=True,
    start_date=evaluation_date_range.start_date,
    end_date=evaluation_date_range.end_date
)
test_sample = ema(
    test_sample,
    source_column="Close",
    period=param_variant["ema_short_period"],
    result_column="ema_short"
)
test_sample = ema(
    test_sample,
    source_column="Close",
    period=param_variant["ema_long_period"],
    result_column="ema_long"
)
test_sample = crossover(
    test_sample,
    first_column="ema_short",
    second_column="ema_long",
    result_column="crossover"
)
test_sample = crossunder(
    test_sample,
    first_column="ema_short",
    second_column="ema_long",
    result_column="crossunder"
)

data = {"ema_data": ema_data, "rsi_data": rsi_data}
buy_signals_vectorized = strategy.buy_signal_vectorized(data)
print("Buy signals count:", buy_signals_vectorized.sum())
ema_data["buy_signal"] = buy_signals_vectorized
sell_signals_vectorized = strategy.sell_signal_vectorized(data)
print("Sell signals count:", sell_signals_vectorized.sum())
ema_data["sell_signal"] = sell_signals_vectorized

fig = go.Figure()
entries = entry_chart(
    ema_data,
    entry_column="buy_signal"
)
exits = exit_chart(
    ema_data,
    exit_column="sell_signal"
)
scatter_crossover, scatter_crossunder = crossover_crossunder_chart(test_sample)
ema_short = line_chart(test_sample, "ema_short")
ema_long = line_chart(test_sample, "ema_long")
price_chart = line_chart(price_data, "Close")

fig.add_trace(price_chart)
fig.add_trace(exits)
fig.add_trace(entries)
fig.add_trace(ema_short)
fig.add_trace(ema_long)
fig.show()

Buy signals count: 19
Sell signals count: 1
